In [ ]:
import pandas as pd
import numpy as np
import datetime
import random
import os
import sys
import holidays


import sklearn
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import KFold


import xgboost
from xgboost import XGBRegressor
import catboost
from catboost import CatBoostRegressor

from optuna.trial import Trial
import optuna

In [ ]:
print(f"파이썬 버전 : {sys.version}")
print(f"pandas 버전 : {pd.__version__}")
print(f"numpy 버전 : {np.__version__}")
print(f"sklearn 버전 : {sklearn.__version__}")
print(f"xgboost 버전 확인 : {xgboost.__version__}")
print(f"catboost 버전 : {catboost.__version__}")
print(f"optuna 버전 : {optuna.__version__}")

In [ ]:
def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)

seed_everything(2024) # Seed 고정

In [ ]:
train = pd.read_csv('/mnt/c/Users/wschu/OneDrive/Documents/data/jeju_specialty/open/train.csv')
test = pd.read_csv('/mnt/c/Users/wschu/OneDrive/Documents/data/jeju_specialty/open/test.csv')
international_data = pd.read_csv('/mnt/c/Users/wschu/OneDrive/Documents/data/jeju_specialty/open/international_trade.csv')

In [ ]:
international_data

In [ ]:
print(international_data['품목명'].value_counts())

In [ ]:
print(international_data['품목명'].unique())

In [ ]:
relevant_dict = {"TG": "감귤", "BC": "꽃양배추와 브로콜리(broccoli)", "RD": None, "CR": "당근", "CB": "양배추"} # RD: 무는 없음

In [ ]:
international_data.columns

In [ ]:
new_column_names = {"기간": "timestamp", "품목명": "item", "수출 중량": "export_weight", "수출 금액": "export_amount", "수입 중량": "import_weight", "수입 금액": "import_amount", "무역수지": "trade_profit"}
international_data.rename(columns=new_column_names, inplace=True)

In [ ]:
international_data['timestamp'] = pd.to_datetime(international_data['timestamp'])

In [ ]:
type(international_data.timestamp[0])

In [ ]:
def change_type(type_):
    result = None
    for key, value in relevant_dict.items():
            if value == type_:
                result = key
                break
    return result

In [ ]:
international_data['item'] = international_data.apply(lambda x: change_type(x['item']), axis=1)

In [ ]:
# data leakage를 피하기 위해 international_data는 2023년 1월분까지만 사용
print(international_data.shape)
international_data = international_data.loc[international_data.timestamp < pd.to_datetime("2023-02-01"), ]
print(international_data.shape)

In [ ]:
scaler = StandardScaler()
international_data.loc[:, ["export_weight", "export_amount", "import_weight", "import_amount", "trade_profit"]] = scaler.fit_transform(international_data.loc[:, ["export_weight", "export_amount", "import_weight", "import_amount", "trade_profit"]])

In [ ]:
international_data

In [ ]:
def pre_all(train, test):
    print(f"전처리 전 train 크기 : {train.shape}")
    print(f"전처리 전 test 크기 : {test.shape}")
    print("=================전처리 중=================")

    # 합쳐서 전처리하기
    train["timestamp"] = pd.to_datetime(train["timestamp"])
    test["timestamp"] = pd.to_datetime(test["timestamp"])
    df = pd.concat([train,test]).reset_index(drop = True)
    
    df.rename(columns={'supply(kg)':'supply', 'price(원/kg)':'price'},inplace=True)

    #년/월/일 추가
    df['year']=df['timestamp'].dt.year
    df['month']=df['timestamp'].dt.month
    df['day']=df['timestamp'].dt.day

    #요일 추가
    df['week_day']=df['timestamp'].dt.weekday

    # 년-월 변수 추가 : year-month의 형태, 개월단위 누적값
    le = LabelEncoder()
    df["year_month"] = df["timestamp"].map(lambda x :str(x.year) + "-"+str(x.month))

    # 라벨 인코딩
    df["year_month"] = le.fit_transform(df["year_month"])


    # 주차 변수 추가
    df["week"] = df["timestamp"].map(lambda x: datetime.datetime(x.year, x.month, x.day).isocalendar()[1])

    # 주차 누적값
    week_list=[]
    for i in range(len(df['year'])) :
        if df['year'][i] == 2019 :
            week_list.append(int(df['week'][i]))
        elif df['year'][i] == 2020 :
            week_list.append(int(df['week'][i])+52)
        elif df['year'][i] == 2021 :
            week_list.append(int(df['week'][i])+52+53)
        elif df['year'][i] == 2022 :
            week_list.append(int(df['week'][i])+52+53+53)
        elif df['year'][i] == 2023 :
            week_list.append(int(df['week'][i])+52+53+53+52)
    df['week_num']= week_list

    # datetime 패키지에서 19년 12월 마지막주가 첫째주로 들어가는거 발견하여 수정
    df.loc[df['timestamp']=='2019-12-30','week_num']=52
    df.loc[df['timestamp']=='2019-12-31','week_num']=52


    # 공휴일 변수 추가
    def make_holi(x):
        kr_holi = holidays.KR()

        if x in kr_holi:
            return 1
        else:
            return 0
        
    df["holiday"] = df["timestamp"].map(lambda x : make_holi(x))

    # 국제 무역 데이터 접합하기
    # subsidiary_data = []
    # for i in range(len(df)):
    #     row = df.iloc[i, :]
    #     item_ = row['item']
    #     row_date = row.timestamp
    #     target = relevant_dict[item_]
    #     if target == None:
    #         subsidiary_data.append([None] * 5)
    #         continue
    #     target_row = international_data.loc[(international_data.type == relevant_dict["TG"]) & (international_data.date_year_month == row_date), ["export_weight", "export_amount", "import_weight", "import_amount", "trade_profit"]]
    #     if target_row.empty:
    #         subsidiary_data.append([None] * 5)
    #         continue
    #     target_row_list = target_row.values.tolist()[0]
    #     subsidiary_data.append(target_row_list)

    # subsidiary_df = pd.DataFrame(subsidiary_data)

    # print(df.shape)
    # print(subsidiary_df.shape)

    # df = pd.concat([df, subsidiary_df], axis=1)
    # df = pd.merge(df, international_data, on=["timestamp", "item"], how="inner")
    df = pd.merge(df, international_data, on=["timestamp", "item"], how="left")

    # train, test 분리하기
    train = df[~df["price"].isnull()].sort_values("timestamp").reset_index(drop = True)
    test = df[df["price"].isnull()].sort_values("timestamp").reset_index(drop=True)


    print(f"전처리 후 train 크기 : {train.shape}")
    print(f"전처리 후 test 크기 : {test.shape}")

    return train, test

In [ ]:
train_pre, test_pre = pre_all(train, test)

In [ ]:
print(train_pre)
print(train_pre.columns)

In [ ]:
print(test_pre)

# 0. TG 외 품목들
### 0-1. 전처리

In [ ]:
## 전처리

# 극 이상치 제거
tg_idx = train_pre[(train_pre["item"]=="TG") & (train_pre["price"]>20000)].index
rd_idx = train_pre[(train_pre["item"]=="RD") & (train_pre["price"]>5000)].index
bc_idx = train_pre[(train_pre["item"]=="BC") & (train_pre["price"]>8000)].index
cb_idx = train_pre[(train_pre["item"]=="CB") & (train_pre["price"]>2300)].index

train_pre.loc[tg_idx,"price"] = train_pre[(train_pre["item"]=="TG") & (train_pre["price"]!=0)]["price"].mean()
train_pre.loc[rd_idx,"price"] = train_pre[(train_pre["item"]=="RD") & (train_pre["price"]!=0)]["price"].mean()
train_pre.loc[bc_idx,"price"] = train_pre[(train_pre["item"]=="BC") & (train_pre["price"]!=0)]["price"].mean()
train_pre.loc[cb_idx,"price"] = train_pre[(train_pre["item"]=="CB") & (train_pre["price"]!=0)]["price"].mean()


# 감귤이 아닌것
print(f"train의 컬럼 : {train_pre.columns}")
print(f"test의 컬럼 : {test_pre.columns}")

train_notg = train_pre[train_pre["item"] !="TG"]
test_notg = test_pre[test_pre["item"] != "TG"]


#인코딩
Xy = pd.get_dummies(train_notg.sort_values(by = ["timestamp"]).reset_index(drop=True).drop(columns = ["supply"]), columns = ["item","corporation","location"])
answer_notg = pd.get_dummies(test_notg.drop(columns = ["timestamp","supply","price"]), columns = [ "item","corporation","location"])
print(Xy.columns)

In [ ]:
def objective_cat(trial: Trial, model, x, y, eval_metric):
    """
    Optuna의 하이퍼파라미터 튜닝을 위한 목적 함수
    
    Parameters:
    - trial: Optuna의 Trial 객체
    - model: 튜닝할 머신러닝 모델
    - x: 입력 데이터
    - y: 타겟 데이터
    - eval_metric: 모델을 평가하기 위한 메트릭
    """
    
    # 모델에 맞는 하이퍼파라미터 범위를 정의합니다.
    # cat = CatBoostRegressor(random_state = 2024, 
    #                             n_estimators = n_estimators, 
    #                             learning_rate = lrs, 
    #                             depth = max_depths, 
    #                             l2_leaf_reg = l2_leaf_reg,
    #                             metric_period = 1000)
    params = {
        'random_state': 2024,
        'thread_count': -1,
        # 'criterion': trial.suggest_categorical('criterion', ['squared_error', 'absolute_error']),
        'n_estimators': trial.suggest_int('n_estimators', 500, 1000, step=100),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.05, step=0.01),
        'depth': trial.suggest_int('depth', 5, 15, step=1),
        'l2_leaf_reg': trial.suggest_int('l2_leaf_reg', 1, 5, step=1),
        # 'max_features': trial.suggest_float('max_features', 0.6, 0.9, step=0.1),
    }

    # 데이터 프레임이나 시리즈 형태의 x와 y를 numpy 배열로 변환합니다.
    x_np = x.values if isinstance(x, pd.DataFrame) else x    
    y_np = y.values if isinstance(y, pd.Series) else y

    results = dict()
    
    # 5-Fold Cross Validation을 정의합니다.
    # fold = KFold(n_splits=5, shuffle=True, random_state=2024)
    
    # 각 Fold에 대해 모델을 학습하고 평가합니다.
    # for i, (train_idx, test_idx) in enumerate(fold.split(x, y)):
    years = [2019, 2020, 2021, 2022]
    for i, year in enumerate(years):
        filtered_df = x[(x['year'] == year) & (x['month'] == 3) & (x['day'].between(4, 31))]
        train_idx = x.index.difference(filtered_df.index)
        test_idx = filtered_df.index

        x_train, y_train = x_np[train_idx], y_np[train_idx]
        x_test, y_test = x_np[test_idx], y_np[test_idx]
        
        # 현재의 하이퍼파라미터 세트로 모델을 생성하고 학습합니다.
        fold_model = model(**params)  
        fold_model.fit(x_train, y_train)
        fold_pred = fold_model.predict(x_test)
        
        # 해당 Fold의 평가 결과를 저장합니다.
        fold_error = eval_metric(y_test, fold_pred)
        
        results[i] = {
            'model': fold_model, 
            'error': fold_error
        }
    
    # 모든 Fold의 평가 결과의 평균을 반환합니다.
    errors = [v['error'] for k, v in results.items()]
    return np.array(errors).mean()

In [ ]:
# 최소화 방향으로 하이퍼 파라미터 학습을 위한 스터디 객체를 생성합니다.
study_cat_no_tg = optuna.create_study(direction='minimize', study_name='cat_regressor_no_tg')

# 하이퍼파라미터 튜닝을 시작합니다.
study_cat_no_tg.optimize(lambda trial: objective_cat(trial,
                                                   CatBoostRegressor,
                                                   Xy.drop(columns = ["timestamp", "ID", "price"]),
                                                   Xy["price"],
                                                   mean_squared_error),
                                                   n_trials=20,
                      )

In [ ]:
def objective_xgb(trial: Trial, model, x, y, eval_metric):
    """
    Optuna의 하이퍼파라미터 튜닝을 위한 목적 함수
    
    Parameters:
    - trial: Optuna의 Trial 객체
    - model: 튜닝할 머신러닝 모델
    - x: 입력 데이터
    - y: 타겟 데이터
    - eval_metric: 모델을 평가하기 위한 메트릭
    """
    
    # 모델에 맞는 하이퍼파라미터 범위를 정의합니다.
    # xgb = XGBRegressor(n_estimators = 1000,
    #                    random_state = 2024,
    #                    learning_rate = 0.01,
    #                    max_depth = 10,
    #                    device='cuda')
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 500, 1000, step=100),
        # 'random_state': 2024,
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.05, step=0.01),
        'max_depth': trial.suggest_int('max_depth', 5, 15, step=1),
        # 'device': 'cuda',
    }

    # 데이터 프레임이나 시리즈 형태의 x와 y를 numpy 배열로 변환합니다.
    x_np = x.values if isinstance(x, pd.DataFrame) else x    
    y_np = y.values if isinstance(y, pd.Series) else y

    results = dict()
    
    years = [2019, 2020, 2021, 2022]
    for i, year in enumerate(years):
        filtered_df = x[(x['year'] == year) & (x['month'] == 3) & (x['day'].between(4, 31))]
        train_idx = x.index.difference(filtered_df.index)
        test_idx = filtered_df.index

        x_train, y_train = x_np[train_idx], y_np[train_idx]
        x_test, y_test = x_np[test_idx], y_np[test_idx]
        
        # 현재의 하이퍼파라미터 세트로 모델을 생성하고 학습합니다.
        fold_model = model(random_state=2024,
                           **params)  
        fold_model.fit(x_train, y_train)
        fold_pred = fold_model.predict(x_test)
        
        # 해당 Fold의 평가 결과를 저장합니다.
        fold_error = eval_metric(y_test, fold_pred)
        
        results[i] = {
            'model': fold_model, 
            'error': fold_error
        }
    
    # 모든 Fold의 평가 결과의 평균을 반환합니다.
    errors = [v['error'] for k, v in results.items()]
    return np.array(errors).mean()

In [ ]:
# 최소화 방향으로 하이퍼 파라미터 학습을 위한 스터디 객체를 생성합니다.
study_xgb_no_tg = optuna.create_study(direction='minimize', study_name='xgb_regressor_no_tg')

# 하이퍼파라미터 튜닝을 시작합니다.
study_xgb_no_tg.optimize(lambda trial: objective_xgb(trial,
                                                   XGBRegressor,
                                                   Xy.drop(columns = ["timestamp", "ID","price"]),
                                                   Xy["price"],
                                                   mean_squared_error),
                                                   n_trials=80,
                      )

In [ ]:
## 앙상블 모델 정의
cat = CatBoostRegressor(random_state = 2024,
                        metric_period = 1000,
                        **study_cat_no_tg.best_params)

xgb = XGBRegressor(random_state = 2024,
                   device='cuda',
                   **study_xgb_no_tg.best_params)

In [ ]:
# voting
vote_model = VotingRegressor(
    estimators =[("cat",cat), ("xgb", xgb)]
)

vote_model.fit(Xy.drop(columns = ["timestamp", "ID", "price"]), Xy["price"])

pred = vote_model.predict(answer_notg.drop(columns = ["ID", "answer"]))
for idx in range(len(pred)):
    if pred[idx]<0:
        pred[idx]= 0
answer_notg["answer"] = pred

answer_notg[["ID","answer"]]

# 1. TG (1)
### 1-1. 전처리

In [151]:
train_pre, test_pre = pre_all(train, test)

# 공휴일이지만 안쉬는 날 제외하기
no_holi = list(train_pre[(train_pre["item"] =="TG") &(train_pre["holiday"]==1) & (train_pre["price"]!=0)].groupby("timestamp").count().reset_index()["timestamp"])
noholi_idx = train_pre[train_pre["timestamp"].isin(no_holi)]["holiday"].index
for idx in noholi_idx:
    train_pre.loc[idx, "holiday"] = 0

# train 및 test 시간 순서로 정렬하기
train_tg = train_pre[train_pre["item"] == "TG"].sort_values(by = ["timestamp"]).reset_index(drop= True)
test_tg = test_pre[test_pre["item"] == "TG"].sort_values(by = ["timestamp"]).reset_index(drop= True)

Xy = pd.get_dummies(train_tg, columns = [ "item","corporation","location"]).drop(columns = ["supply"])
answer_tg1 = pd.get_dummies(test_tg, columns = [ "item","corporation","location"]).drop(columns = ["timestamp","supply","price"])
print(f"train의 컬럼 : {Xy.columns}")
print(f"test의 컬럼 : {answer_tg1.columns}")
Xy["price"] = np.sqrt(Xy["price"])

전처리 전 train 크기 : (59397, 7)
전처리 전 test 크기 : (1092, 5)
=================전처리 중=================
전처리 후 train 크기 : (59397, 20)
전처리 후 test 크기 : (1092, 20)
train의 컬럼 : Index(['ID', 'timestamp', 'price', 'year', 'month', 'day', 'week_day',
       'year_month', 'week', 'week_num', 'holiday', 'export_weight',
       'export_amount', 'import_weight', 'import_amount', 'trade_profit',
       'item_TG', 'corporation_A', 'corporation_B', 'corporation_C',
       'corporation_D', 'corporation_E', 'location_J', 'location_S'],
      dtype='object')
test의 컬럼 : Index(['ID', 'year', 'month', 'day', 'week_day', 'year_month', 'week',
       'week_num', 'holiday', 'export_weight', 'export_amount',
       'import_weight', 'import_amount', 'trade_profit', 'item_TG',
       'corporation_A', 'corporation_B', 'corporation_C', 'corporation_D',
       'corporation_E', 'location_J', 'location_S'],
      dtype='object')


### 3-2. 모델링 & 훈련 예측

In [152]:
# 최소화 방향으로 하이퍼 파라미터 학습을 위한 스터디 객체를 생성합니다.
study_cat_tg = optuna.create_study(direction='minimize', study_name='cat_regressor_tg')

# 하이퍼파라미터 튜닝을 시작합니다.
study_cat_tg.optimize(lambda trial: objective_cat(trial,
                                                   CatBoostRegressor,
                                                   Xy.drop(columns = ["timestamp", "ID", "price"]),
                                                   Xy["price"],
                                                   mean_squared_error),
                                                   n_trials=20,
                      )

study_xgb_tg = optuna.create_study(direction='minimize', study_name='xgb_regressor_tg')

# 하이퍼파라미터 튜닝을 시작합니다.
study_xgb_tg.optimize(lambda trial: objective_xgb(trial,
                                                   XGBRegressor,
                                                   Xy.drop(columns = ["timestamp", "ID", "price"]),
                                                   Xy["price"],
                                                   mean_squared_error),
                                                   n_trials=20,
                      )

[I 2024-03-28 19:20:12,610] A new study created in memory with name: cat_regressor_tg


0:	learn: 30.8074600	total: 1.31ms	remaining: 786ms
1:	learn: 30.4481477	total: 8.07ms	remaining: 2.41s
2:	learn: 30.1009041	total: 14.2ms	remaining: 2.83s
3:	learn: 29.7506784	total: 20.4ms	remaining: 3.04s
4:	learn: 29.4295596	total: 23.5ms	remaining: 2.8s
5:	learn: 29.1273507	total: 24.9ms	remaining: 2.46s
6:	learn: 28.8082572	total: 31.1ms	remaining: 2.64s
7:	learn: 28.5055680	total: 37.8ms	remaining: 2.8s
8:	learn: 28.2176856	total: 41ms	remaining: 2.69s
9:	learn: 27.9421693	total: 42.4ms	remaining: 2.5s
10:	learn: 27.6678230	total: 48.6ms	remaining: 2.6s
11:	learn: 27.3925184	total: 51.3ms	remaining: 2.51s
12:	learn: 27.1348712	total: 56.7ms	remaining: 2.56s
13:	learn: 26.8791884	total: 58.8ms	remaining: 2.46s
14:	learn: 26.6121076	total: 63.9ms	remaining: 2.49s
15:	learn: 26.3680723	total: 69.1ms	remaining: 2.52s
16:	learn: 26.1176103	total: 74.7ms	remaining: 2.56s
17:	learn: 25.8957884	total: 80.3ms	remaining: 2.6s
18:	learn: 25.6642827	total: 85.7ms	remaining: 2.62s
19:	learn:

[I 2024-03-28 19:20:26,100] Trial 0 finished with value: 300.1993210979238 and parameters: {'n_estimators': 600, 'learning_rate': 0.02, 'depth': 11, 'l2_leaf_reg': 2}. Best is trial 0 with value: 300.1993210979238.


575:	learn: 14.9068847	total: 3.08s	remaining: 129ms
576:	learn: 14.9032593	total: 3.09s	remaining: 123ms
577:	learn: 14.8986890	total: 3.1s	remaining: 118ms
578:	learn: 14.8920629	total: 3.1s	remaining: 113ms
579:	learn: 14.8873667	total: 3.11s	remaining: 107ms
580:	learn: 14.8831368	total: 3.11s	remaining: 102ms
581:	learn: 14.8798403	total: 3.12s	remaining: 96.5ms
582:	learn: 14.8745827	total: 3.13s	remaining: 91.2ms
583:	learn: 14.8694196	total: 3.13s	remaining: 85.8ms
584:	learn: 14.8648665	total: 3.14s	remaining: 80.5ms
585:	learn: 14.8586965	total: 3.14s	remaining: 75.1ms
586:	learn: 14.8551743	total: 3.15s	remaining: 69.7ms
587:	learn: 14.8513703	total: 3.15s	remaining: 64.4ms
588:	learn: 14.8454145	total: 3.16s	remaining: 59ms
589:	learn: 14.8401819	total: 3.17s	remaining: 53.6ms
590:	learn: 14.8354886	total: 3.17s	remaining: 48.3ms
591:	learn: 14.8323112	total: 3.18s	remaining: 42.9ms
592:	learn: 14.8281104	total: 3.18s	remaining: 37.6ms
593:	learn: 14.8246142	total: 3.19s	re

[I 2024-03-28 19:21:04,289] Trial 1 finished with value: 309.61651239917126 and parameters: {'n_estimators': 500, 'learning_rate': 0.04, 'depth': 13, 'l2_leaf_reg': 5}. Best is trial 0 with value: 300.1993210979238.


...

[I 2024-03-28 19:34:47,364] Trial 18 finished with value: 288.07922741820164 and parameters: {'n_estimators': 800, 'learning_rate': 0.03, 'depth': 6, 'l2_leaf_reg': 2}. Best is trial 10 with value: 287.3358266924869.


677:	learn: 16.2004227	total: 580ms	remaining: 104ms
678:	learn: 16.1977127	total: 581ms	remaining: 104ms
679:	learn: 16.1957070	total: 582ms	remaining: 103ms
680:	learn: 16.1918929	total: 583ms	remaining: 102ms
681:	learn: 16.1892499	total: 583ms	remaining: 101ms
682:	learn: 16.1860538	total: 584ms	remaining: 100ms
683:	learn: 16.1845005	total: 585ms	remaining: 99.2ms
684:	learn: 16.1828798	total: 586ms	remaining: 98.4ms
685:	learn: 16.1804901	total: 587ms	remaining: 97.5ms
686:	learn: 16.1783561	total: 588ms	remaining: 96.7ms
687:	learn: 16.1757494	total: 589ms	remaining: 95.8ms
688:	learn: 16.1730628	total: 589ms	remaining: 94.9ms
689:	learn: 16.1725392	total: 590ms	remaining: 94.1ms
690:	learn: 16.1715683	total: 591ms	remaining: 93.2ms
691:	learn: 16.1704916	total: 592ms	remaining: 92.4ms
692:	learn: 16.1671123	total: 593ms	remaining: 91.5ms
693:	learn: 16.1658146	total: 594ms	remaining: 90.7ms
694:	learn: 16.1636939	total: 595ms	remaining: 89.8ms
695:	learn: 16.1614787	total: 596m

[I 2024-03-28 19:34:52,307] Trial 19 finished with value: 291.8686818855866 and parameters: {'n_estimators': 900, 'learning_rate': 0.02, 'depth': 8, 'l2_leaf_reg': 4}. Best is trial 10 with value: 287.3358266924869.
[I 2024-03-28 19:34:52,307] A new study created in memory with name: xgb_regressor_tg


780:	learn: 15.8135572	total: 979ms	remaining: 149ms
781:	learn: 15.8132296	total: 980ms	remaining: 148ms
782:	learn: 15.8106200	total: 981ms	remaining: 147ms
783:	learn: 15.8076188	total: 983ms	remaining: 145ms
784:	learn: 15.8042223	total: 984ms	remaining: 144ms
785:	learn: 15.8017090	total: 985ms	remaining: 143ms
786:	learn: 15.7984518	total: 987ms	remaining: 142ms
787:	learn: 15.7981851	total: 988ms	remaining: 140ms
788:	learn: 15.7949675	total: 990ms	remaining: 139ms
789:	learn: 15.7909122	total: 991ms	remaining: 138ms
790:	learn: 15.7905930	total: 992ms	remaining: 137ms
791:	learn: 15.7873808	total: 994ms	remaining: 136ms
792:	learn: 15.7857246	total: 996ms	remaining: 134ms
793:	learn: 15.7840744	total: 997ms	remaining: 133ms
794:	learn: 15.7804018	total: 1000ms	remaining: 132ms
795:	learn: 15.7790163	total: 1s	remaining: 131ms
796:	learn: 15.7764923	total: 1s	remaining: 130ms
797:	learn: 15.7753993	total: 1s	remaining: 128ms
798:	learn: 15.7722889	total: 1.01s	remaining: 127ms
7

[I 2024-03-28 19:34:56,251] Trial 0 finished with value: 305.0655482229911 and parameters: {'n_estimators': 500, 'learning_rate': 0.02, 'max_depth': 8}. Best is trial 0 with value: 305.0655482229911.
[I 2024-03-28 19:35:01,073] Trial 1 finished with value: 290.60122203190883 and parameters: {'n_estimators': 900, 'learning_rate': 0.03, 'max_depth': 6}. Best is trial 1 with value: 290.60122203190883.
[I 2024-03-28 19:35:08,753] Trial 2 finished with value: 312.71145971533406 and parameters: {'n_estimators': 1000, 'learning_rate': 0.03, 'max_depth': 8}. Best is trial 1 with value: 290.60122203190883.
[I 2024-03-28 19:35:22,189] Trial 3 finished with value: 390.01038607193135 and parameters: {'n_estimators': 600, 'learning_rate': 0.02, 'max_depth': 14}. Best is trial 1 with value: 290.60122203190883.
[I 2024-03-28 19:35:45,583] Trial 4 finished with value: 404.38787060959515 and parameters: {'n_estimators': 1000, 'learning_rate': 0.05, 'max_depth': 15}. Best is trial 1 with value: 290.6012

In [156]:
print(study_cat_tg.best_params)
print(study_xgb_tg.best_params)

{'n_estimators': 800, 'learning_rate': 0.03, 'depth': 6, 'l2_leaf_reg': 3}
{'n_estimators': 900, 'learning_rate': 0.03, 'max_depth': 6}


In [157]:
cat = CatBoostRegressor(random_state = 2024,
                        metric_period = 1000,
                        **study_cat_tg.best_params)

xgb = XGBRegressor(random_state = 2024,
                   device='cuda',
                   **study_xgb_tg.best_params)

In [159]:
# voting
vote_model = VotingRegressor(
    estimators =[("cat",cat), ("xgb", xgb)]
)

vote_model.fit(Xy.drop(columns = ["timestamp", "ID","price"]), Xy["price"])

pred = vote_model.predict(answer_tg1.drop(columns = ["ID"]))
for idx in range(len(pred)):
    if pred[idx]<0:
        pred[idx]= 0
answer_tg1["answer"] = np.power(pred,2)

answer_tg1[["ID","answer"]]

0:	learn: 30.6073935	total: 1.3ms	remaining: 1.04s
799:	learn: 16.0157061	total: 726ms	remaining: 0us
[19:38:48] WARNING: /croot/xgboost-split_1675457761144/work/src/learner.cc:767: 
Parameters: { "device" } are not used.



ID       answer
0    TG_A_J_20230304  2769.258597
1    TG_E_S_20230304  3371.770351
2    TG_E_J_20230304  1247.973414
3    TG_D_S_20230304  3674.167752
4    TG_D_J_20230304   324.027678
..               ...          ...
275  TG_D_J_20230331  1142.198745
276  TG_D_S_20230331  5159.619945
277  TG_A_S_20230331  5839.199820
278  TG_E_S_20230331  4820.895274
279  TG_E_J_20230331  1872.705455

[280 rows x 2 columns]

# 4. TG (2)
- 일반화를 위한 추가 모델링
### 4-1. 전처리

In [160]:
train_tg2 = train_pre[train_pre["item"] =="TG"]
test_tg2 = test_pre[test_pre["item"] == "TG"]

Xy2 = pd.get_dummies(train_tg2.sort_values(by = ["timestamp", "corporation","location"]).reset_index(drop=True).drop(columns = ["item","supply"]), columns = [ "corporation","location"])
answer_tg2 = pd.get_dummies(test_tg2.drop(columns = ["timestamp","supply","price","item"]), columns = [ "corporation","location"])
print(Xy2.columns)

# 종속변수 루트값
Xy2["price"] = np.sqrt(Xy2["price"])

Index(['ID', 'timestamp', 'price', 'year', 'month', 'day', 'week_day',
       'year_month', 'week', 'week_num', 'holiday', 'export_weight',
       'export_amount', 'import_weight', 'import_amount', 'trade_profit',
       'corporation_A', 'corporation_B', 'corporation_C', 'corporation_D',
       'corporation_E', 'location_J', 'location_S'],
      dtype='object')


### 4-2. 모델링 & 훈련 예측

In [162]:
study_xgb_tg_2 = optuna.create_study(direction='minimize', study_name='xgb_regressor_tg_2')

# 하이퍼파라미터 튜닝을 시작합니다.
study_xgb_tg_2.optimize(lambda trial: objective_xgb(trial,
                                                   XGBRegressor,
                                                   Xy2.drop(columns = ["timestamp", "ID", "price"]),
                                                   Xy2["price"],
                                                   mean_squared_error),
                                                   n_trials=30,
                      )

[I 2024-03-28 19:40:24,885] A new study created in memory with name: xgb_regressor_tg_2
[I 2024-03-28 19:40:27,494] Trial 0 finished with value: 295.068835676664 and parameters: {'n_estimators': 500, 'learning_rate': 0.01, 'max_depth': 6}. Best is trial 0 with value: 295.068835676664.
[I 2024-03-28 19:40:31,057] Trial 1 finished with value: 307.914325277217 and parameters: {'n_estimators': 700, 'learning_rate': 0.05, 'max_depth': 6}. Best is trial 0 with value: 295.068835676664.
[I 2024-03-28 19:40:34,663] Trial 2 finished with value: 295.53720266238633 and parameters: {'n_estimators': 700, 'learning_rate': 0.04, 'max_depth': 6}. Best is trial 0 with value: 295.068835676664.
[I 2024-03-28 19:40:39,039] Trial 3 finished with value: 321.0932221916768 and parameters: {'n_estimators': 500, 'learning_rate': 0.03, 'max_depth': 9}. Best is trial 0 with value: 295.068835676664.
[I 2024-03-28 19:40:54,914] Trial 4 finished with value: 393.62063971768293 and parameters: {'n_estimators': 600, 'le

In [163]:
# 모델 정의 및 훈련 예측
cat = CatBoostRegressor(random_state = 2024,
                        metric_period = 1000,
                        l2_leaf_reg = 3,
                        **study_xgb_tg_2.best_params)
cat.fit(Xy2.drop(columns = ["timestamp", "ID", "price"]), Xy2["price"])

pred2 = cat.predict(answer_tg2.drop(columns = ["ID"]))
for idx in range(len(pred2)):
    if pred2[idx]<0:
        pred2[idx]= 0
answer_tg2["answer"] = np.power(pred2,2)

answer_tg2[["ID","answer"]]

0:	learn: 30.9627769	total: 1.03ms	remaining: 825ms
799:	learn: 17.5576027	total: 621ms	remaining: 0us


ID       answer
0     TG_A_J_20230304  2649.827660
1     TG_E_S_20230304  3051.385401
3     TG_E_J_20230304  1308.403333
5     TG_D_S_20230304  3431.358627
8     TG_D_J_20230304  2124.296045
...               ...          ...
1074  TG_D_S_20230331  4703.574936
1077  TG_A_S_20230331  5096.694778
1079  TG_E_S_20230331  4156.976128
1087  TG_A_J_20230331  3819.401204
1090  TG_E_J_20230331  1807.031153

[280 rows x 2 columns]

# 5. TG 앙상블

In [164]:
total1 = pd.concat([answer_tg1[["ID","answer"]],answer_notg[["ID","answer"]]])
total2 = pd.concat([answer_tg2[["ID","answer"]],answer_notg[["ID","answer"]]])

In [165]:
print(total1.shape)
print(total2.shape)

(1092, 2)
(1092, 2)


In [166]:
# TG 앙상블 (평균)

df = pd.merge(total1, total2, how = "inner", on="ID")

In [167]:
df

ID     answer_x     answer_y
0     TG_A_J_20230304  2769.258597  2649.827660
1     TG_E_S_20230304  3371.770351  3051.385401
2     TG_E_J_20230304  1247.973414  1308.403333
3     TG_D_S_20230304  3674.167752  3431.358627
4     TG_D_J_20230304   324.027678  2124.296045
...               ...          ...          ...
1087  RD_D_S_20230331   536.485698   536.485698
1088  CR_C_J_20230331  1912.146164  1912.146164
1089  RD_D_J_20230331   293.934552   293.934552
1090  CR_D_J_20230331  2015.732452  2015.732452
1091  RD_F_J_20230331   567.710972   567.710972

[1092 rows x 3 columns]

In [168]:

df["answer"] = (df["answer_x"]+df["answer_y"])/2
df["item"] = df["ID"].map(lambda x :x.split("_")[0])

In [169]:
# 후처리 
## 전체 min값 | 3월의 min값 확인
df.loc[(df['item']=='TG')&(df['answer']<400),'answer'] =0 # 551   #3월 675
df.loc[(df['item']=='CB')&(df['answer']<50),'answer'] =0 # 162  # 3월 200
df.loc[(df['item']=='RD')&(df['answer']<10),'answer'] =0 # 50     # 3월 124
df.loc[(df['item']=='CR')&(df['answer']<150),'answer'] =0 # 250   # 3월 450
df.loc[(df['item']=='BC')&(df['answer']<100),'answer'] =0 #205 3월 205.0

In [170]:
df = df.drop(columns = ["answer_x","answer_y", "item"])
df

ID       answer
0     TG_A_J_20230304  2709.543128
1     TG_E_S_20230304  3211.577876
2     TG_E_J_20230304  1278.188374
3     TG_D_S_20230304  3552.763190
4     TG_D_J_20230304  1224.161862
...               ...          ...
1087  RD_D_S_20230331   536.485698
1088  CR_C_J_20230331  1912.146164
1089  RD_D_J_20230331   293.934552
1090  CR_D_J_20230331  2015.732452
1091  RD_F_J_20230331   567.710972

[1092 rows x 2 columns]

In [171]:
# 제출용
df.to_csv('/mnt/c/Users/wschu/OneDrive/Documents/data/jeju_specialty/open/answer.csv',index=False)